# Example: fit a baseline

## Load the libraries and create a signal


In [1]:
# load libraries
%matplotlib inline
import numpy as np
import rampy

# the following code is for the rendering of plotly graphs in Rampy docs, you don't need it
# Set renderer for Jupyter notebooks
import plotly.io as pio
pio.renderers.default = 'notebook'

# create signal
nb_points = 500
x = np.linspace(50, 500, nb_points)

# gaussian peaks
p1 = 20.0 * np.exp(-np.log(2) * ((x-150.0)/15.0)**2)
p2 = 100.0 * np.exp(-np.log(2) * ((x-250.0)/5.0)**2)
p3 = 50.0 * np.exp(-np.log(2) * ((x-450.0)/1.0)**2)
p4 = 20.0 * np.exp(-np.log(2) * ((x-350.0)/30.0)**2)
p5 = 30.0 * np.exp(-np.log(2) * ((x-460.0)/5.0)**2)

# background: a large sin distortion + linear 
bkg = 10*np.sin(x/50) + 0.1*x

#noise
noise = 2.0 * np.random.normal(size=nb_points)

#observation
y = p1 + p2 + p3 + p4 + p5 + noise +bkg

# we use the rampy API (plotly behind it!) to plot the spectrum
fig = rampy.plot_spectrum(x, y, title = "our spectrum", xaxis_title="X", yaxis_title="Y")
fig.show()

## Now using different baselines to retrieve the true background

We also use the plot_spectrum function to show the different baselines.

In [3]:
# need to define some fitting regions for the spline
roi = [[0,100],[200,220],[280, 290],[420,430],[480,500]]

# calculating the baselines
ycalc_poly, base_poly = rampy.baseline(x, y, roi=roi, method='poly', polynomial_order=4)
ycalc_gcvspl, base_gcvspl = rampy.baseline(x,y, roi=roi, method='gcvspline')
ycalc_uni, base_uni = rampy.baseline(x, y, roi=roi, method='unispline', s=1.2)
ycalc_als, base_als = rampy.baseline(x, y, method='als', lam=10**5, p=0.05)
ycalc_arpls, base_arpsl = rampy.baseline(x, y, method='arPLS', lam=10**6, ratio=0.001)
ycalc_drpls, base_drpsl = rampy.baseline(x, y, method='drPLS', lam=10**6)
ycalc_rubberband, base_rubberband = rampy.baseline(x, y, method='rubberband')
ycalc_whittaker, base_whittaker = rampy.baseline(x, y, roi=roi, method='whittaker', lam=10**5)

# doing the figure
fig = rampy.plot_spectrum(x, y, baselines=[base_poly, base_gcvspl, base_uni, base_als, base_arpsl, base_drpsl, base_rubberband, base_whittaker],
                          baseline_labels=['poly', 'gcvspline', 'unispline', 'als', 'arPLS', 'drPLS', 'rubberband', 'whittaker'],
                          title = "Various baseline comparison", xaxis_title="X", yaxis_title="Y")
fig.show()


# Automatic selection of smoothing coefficient for GCV spline

For the GCV spline, we can forget about the s parameter and it will be determined using the GCV method, or we can set it to a desired value. Here is a comparison:

In [4]:
# calculating the baselines
ycalc_gcvspl, base_gcvspl = rampy.baseline(x, y, roi=roi, method='gcvspline')
ycalc_gcvspl_2, base_gcvspl_2 = rampy.baseline(x, y, roi=roi, method='gcvspline', s=1.0)

# figure
fig = rampy.plot_spectrum(x, y, 
                          baselines=[base_gcvspl, base_gcvspl_2],
                          baseline_labels=['s calculated by GCV', 'manual s'],
                          title = "Comparing manual and GCV smoothing splines for baselines", xaxis_title="X", yaxis_title="Y")
fig.show()

## Machine learning baseline!

You can use a Gaussian process to fit the baseline.

In [5]:
# calculating the baselines
ycalc_GP, base_GP = rampy.baseline(x, y, method='GP', roi=roi)

# figure
fig = rampy.plot_spectrum(x, y, 
                          baselines=[base_gcvspl, base_GP],
                          baseline_labels=['GCV spline', 'Gaussian Process'],
                          title = "Comparing GCV smoothing spline and Gaussian Process baselines", xaxis_title="X", yaxis_title="Y")
fig.show()